In [4]:
%load_ext autoreload
%autoreload 2

The autoreload extension is already loaded. To reload it, use:
  %reload_ext autoreload


In [11]:
import json
from tqdm import tqdm_notebook as tqdm
from scipy.stats import pearsonr
import pandas as pd
import numpy as np
import os
from BasicModel import BasicModel

In [12]:
filepath = './datasets'
processed_dataset_filepath = './processed_data'
gauge_path = filepath+'/gauge.csv'
radar_path = filepath+'/radar'
station_location_path = processed_dataset_filepath +'/station_location.json'

In [13]:
with open(station_location_path, 'r') as infile:
    station_location = json.load(infile)

In [ ]:
df_gauge = pd.read_csv(gauge_path)

In [ ]:
df_gauge_array = df_gauge.values[:, 2:]
print (df_gauge_array.shape)

In [ ]:
np.where(pd.isnull(df_gauge))

In [ ]:
all_radar_path_list = sorted(os.listdir(radar_path))

In [ ]:
df_gauge.head()
df_gauge['Week'] = df_gauge['Week'].astype(str)

In [ ]:
train_week = []
list_dfs = []
for filename in tqdm(all_radar_path_list):
    week = filename.split('.')[0][-2:]
    train_week.append(str(week))
    full_radar_path = os.path.join(radar_path, filename)
    df_radar = pd.read_csv(full_radar_path)
    df_radar['latlong'] = df_radar['lat'] * 1000 + df_radar['long']
    list_dfs.append(df_radar)

In [ ]:
df_result = pd.DataFrame(columns = column_names)
for station in tqdm(range(df_gauge_array.shape[1])):
    for week in train_week:
        chosen_latlong = int(station_location[str(station)]['latlong'])
        y = df_gauge[df_gauge['Week'] == str(week)][str(station)].values[0]
        week_index = train_week.index(week)
        df_radar = list_dfs[week_index]
        x = df_radar[df_radar['latlong'] == chosen_latlong].values[:, 2:36][0]
        df_row = pd.DataFrame([np.concatenate(([station], [week], x, [y]))], columns = column_names)
        df_result = pd.concat([df_result, df_row])      

In [ ]:
df_result.to_csv('./preprocessed_data/train.csv', index=False)

In [14]:
train_path = processed_dataset_filepath+'/train.csv'

In [17]:
df_result = pd.read_csv(train_path)
del df_result['Unnamed: 0']

In [18]:
df_result.head()

station  week     0  1  2  3  4  5  6  7  ...    25  26  27  28  29  30  \
0        0    13  1985  0  3  0  1  1  0  4  ...     0   0   0   0   0   0   
1        0    15  1993  0  0  1  0  0  2  0  ...     0   0   0   0   0   0   
2        0    16  1945  1  1  0  3  4  4  2  ...     0   0   0   0   0   0   
3        0    17  1976  0  0  0  0  0  1  0  ...     0   0   0   0   0   0   
4        0    18  2005  0  0  0  0  1  0  1  ...     0   0   0   0   0   0   

   31  32  33      y  
0   0   0   0   36.8  
1   0   0   0   43.8  
2   0   0   0   98.8  
3   0   0   0  100.2  
4   0   0   0    2.0  

[5 rows x 37 columns]

In [19]:
X_array = df_result.values[:,2:36].astype(float)
y_array = df_result.values[:, 36].astype(float)

In [36]:
basicmodel = BasicModel()

In [37]:
basicmodel.loss(3., .34, X_array, y_array)

522650849.0630083

In [38]:
basicmodel.predict(X_array)

array([ 1397.60762196,  1366.82310835,  3814.47871354, ...,
         567.18886523, 14440.36820761,  7640.9016897 ])

In [39]:
basicmodel.fit(X_array, y_array)

Initial_loss: 522650849.0630083
Shape of x: (1550, 34)
Shape of y: (1550,)
0
349258846.1201786
27608090871.554764
344208763.7158559
27201415369.632824
339305775.03238064
26806660446.604633
334543504.74366814
26423307527.604794
329915941.98345697
26050867759.03809
325417414.6079866
25688879905.693333
321042565.6130326
25336908424.149265
316786331.49753773
24994541695.450027
312643922.3886666
24661390401.88032
308610803.7630115
24337086034.30238
304682679.6161761
24021279517.9521
300855476.94841695
23713639945.857952
297125331.4476638
23413853410.1657
293488574.2633491
23121621922.64329
289941719.77516323
22836662416.517323
286481454.2704046
22558705822.57425
283104625.452036
22287496213.15215
279808232.7071153
22022790008.267544
276589418.07200176
21764355238.67322
273445457.83674526
21511970861.135593
270373754.73645145
21265426121.660404
267371830.68224263
21024519962.79175
264437319.98874742
20789060471.461834
261567963.05895925
20558864364.18924
258761600.4907725
20333756506.70731
2

4817961542.698079
63495379.7432184
4805825297.640937
63341140.21737252
4793750652.491176
63187673.71411607
4781737138.196649
63034974.39578833
4769784290.461459
62883036.48354355
4757891649.6858
62731854.25661016
4746058760.906653
62581422.051562525
4734285173.739453
62431734.26160234
4722570442.320576
62282785.33585173
4710914125.250704
62134569.77865648
4699315785.539062
61987082.148899496
4687774990.548443
61840317.05932528
4676291311.941125
61694269.17587349
4664864325.625509
61548933.21702282
4653493611.703612
61404303.95314503
4642178754.419325
61260376.2058676
4630919342.107429
61117144.84744636
4619714967.143346
60974604.80014715
4608565225.893654
60832751.03563628
4597469718.667312
60691578.57438077
4586428049.667633
60551082.48505594
4575439826.944883
60411257.883963205
4564504662.349681
60272099.934454635
4553622171.48695
60133603.84636743
4542791973.670657
59995764.87546537
4532013691.879106
59858578.32288889
4521286952.71095
59722039.53461255
4510611386.341757
59586143.900

36875396.5421204
2733255772.7124434
36825431.26139444
2729392830.986717
36775606.92931051
2725540917.7568946
36725922.94548029
2721699985.7290177
36676378.712932505
2717869987.8795176
36626973.63808838
2714050877.4532785
36577707.13073754
2710242607.9617076
36528578.60401436
2706445133.1808705
36479587.47437382
2702658407.1495743
36430733.16156847
2698882384.1675286
36382015.088624805
2695117018.79348
36333432.681820266
2691362265.8433805
36284985.37066028
2687618080.3885674
36236672.58785576
2683884417.7539725
36188493.76930027
2680161233.516318
36140448.35404794
2676448483.502356
36092535.78429111
2672746123.7871003
36044755.505338535
2669054110.692086
35997106.965593636
2665372400.7836547
35949589.61653275
2661700950.871222
35902202.91268377
2658039718.005582
35854946.311605036
2654388659.4772353
35807819.2738641
2650747732.8146977
35760821.263017036
2647116895.782867
35713951.74558746
2643496106.381348
35667210.191046305
2639885322.842856
35620596.07179126
2636284503.6315784
355741

25630230.906263206
1867732742.4234555
25606875.93969058
1865944641.7373064
25583565.608684693
1864160004.9593253
25560299.78425439
1862378822.0036387
25537078.337906986
1860601082.8235383
25513901.141645752
1858826777.4112988
25490768.06796767
1857055895.7979875
25467678.989860922
1855288428.0532734
25444633.780802555
1853524364.2852452
25421632.3147562
1851763694.6402204
25398674.466169663
1850006409.3025694
25375760.10997252
1848252498.494514
25352889.121574014
1846501952.4759688
25330061.37686055
1844754761.5443428
25307276.7521935
1843010916.0343595
25284535.12440688
1841270406.3178847
25261836.37080527
1839533222.8037527
25239180.36916125
1837799355.93757
25216566.997713424
1836068796.2015574
25193996.135164067
1834341534.1143632
25171467.660677016
1832617560.2308996
25148981.453875307
1830896865.142155
25126537.394839246
1829179439.47504
25104135.364103902
1827465273.8921952
25081775.24265734
1825754359.0918443
25059456.911938094
1824046685.8076005
25037180.253833294
1822342244.8

Exception ignored in: <object repr() failed>
Traceback (most recent call last):
  File "/home/max/project/data_science_2018/venv/lib/python3.5/site-packages/tqdm/_tqdm.py", line 835, in __del__
    self.close()
  File "/home/max/project/data_science_2018/venv/lib/python3.5/site-packages/tqdm/_tqdm.py", line 1053, in close
    pos = self.pos
AttributeError: 'tqdm' object has no attribute 'pos'


...

761414.30382791
31112388.864489447
761407.6542046
31111992.18294019
761401.0047498313
31111595.512031764
761394.3554635985
31111198.85176373
761387.7063458936
31110802.20213562
761381.0573967102
31110405.563147023
761374.408616042
31110008.9347975
761367.7600038821
31109612.317086596
761361.1115602237
31109215.710013926
761354.4632850612
31108819.113579042
761347.8151783869
31108422.527781505
761341.1672401943
31108025.952620875
761334.5194704768
31107629.388096716
761327.8718692278
31107232.834208596
761321.2244364406
31106836.290956095
761314.577172109
31106439.75833879
761307.9300762261
31106043.236356243
761301.2831487851
31105646.725008
761294.6363897789
31105250.22429364
761287.9897992015
31104853.734212708
761281.3433770463
31104457.25476481
761274.6971233065
31104060.785949502
761268.0510379756
31103664.327766366
761261.4051210466
31103267.880214926
761254.7593725134
31102871.443294797
761248.1137923691
31102475.01700553
761241.468380606
31102078.601346653
761234.8231372196
311

31021431.47006211
759882.7047126405
31021037.224545036
759876.0938465679
31020642.989569817
759869.4831475109
31020248.765136026
759862.8726154631
31019854.55124326
759856.2622504175
31019460.347891044
759849.6520523673
31019066.155078992
759843.0420213065
31018671.972806644
759836.4321572282
31018277.8010736
759829.8224601254
31017883.6398794
759823.2129299922
31017489.489223655
759816.6035668226
31017095.349105936
759809.9943706082
31016701.21952576
759803.3853413444
31016307.10048276
759796.7764790233
31015912.991976492
759790.1677836392
31015518.894006535
759783.5592551846
31015124.80657242
759776.9508936532
31014730.729673743
759770.3426990389
31014336.663310103
759763.7346713357
31013942.60748106
759757.1268105354
31013548.562186163
759750.5191166326
31013154.527425017
759743.9115896206
31012760.503197167
759737.3042294928
31012366.4895022
759730.6970362423
31011972.486339714
759724.090009863
31011578.493709248
759717.4831503482
31011184.511610392
759710.8764576908
31010790.54004

758366.5907628667
30930639.935770154
758360.0181380983
30930248.114111535
758353.4456788442
30929856.302896656
758346.8733850971
30929464.50212501
758340.301256852
30929072.71179623
758333.7292941018
30928680.93190994
758327.1574968391
30928289.162465606
758320.5858650586
30927897.403462905
758314.014398753
30927505.654901378
758307.4430979167
30927113.916780613
758300.8719625431
30926722.189100187
758294.300992625
30926330.471859675
758287.7301881561
30925938.76505864
758281.1595491304
30925547.068696685
758274.5890755412
30925155.38277338
758268.0187673811
30924763.707288284
758261.4486246451
30924372.04224098
758254.8786473261
30923980.38763108
758248.3088354176
30923588.74345814
758241.7391889135
30923197.109721746
758235.1697078065
30922805.48642147
758228.6003920904
30922413.873556875
758222.0312417594
30922022.271127533
758215.462256806
30921630.679133072
758208.8934372247
30921239.09757303
758202.3247830078
30920847.526446998
758195.7562941496
30920455.965754516
758189.18797064

30837679.991245937
756800.426304224
30837290.643333565
756793.893053637
30836901.305765055
756787.3599670241
30836511.97854002
756780.8270443783
30836122.66165801
756774.2942856934
30835733.355118606
756767.7616909624
30835344.05892139
756761.2292601798
30834954.773065973
756754.6969933385
30834565.497551914
756748.1648904325
30834176.2323788
756741.6329514554
30833786.977546226
756735.1011764007
30833397.733053777
756728.569565262
30833008.49890103
756722.038118033
30832619.275087543
756715.5068347069
30832230.061612945
756708.9757152777
30831840.858476803
756702.4447597392
30831451.665678687
756695.9139680844
30831062.483218174
756689.3833403072
30830673.311094865
756682.8528764012
30830284.149308342
756676.3225763595
30829894.997858163
756669.7924401766
30829505.856743965
756663.2624678453
30829116.725965302
756656.7326593604
30828727.605521757
756650.203014714
30828338.495412897
756643.6735339008
30827949.395638328
756637.1442169137
30827560.306197625
756630.6150637465
30827171.227

KeyboardInterrupt: 

In [ ]:
basicmodel.predict(X_array)

In [ ]:
y_array